In [1]:
import sys
import os

# Add the parent directory to sys.path
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '..')))

# Now you can import the module
import initialise as init

In [2]:
# read in the json file
parent_directory = os.path.abspath(os.path.join(os.getcwd(), '..'))
json_file_path = os.path.join(parent_directory, 'simplified_australia_gadm2.json') #'australia_gadm2.geojson
adm2_json = init.gpd.read_file(json_file_path)

print(adm2_json.columns)

Index(['fid', 'gid', 'id_0', 'iso', 'name_0', 'id_1', 'name_1', 'id_2',
       'name_2', 'geometry'],
      dtype='object')


In [3]:
# read in the tsv files
jan_data = init.pd.read_csv('ipobs-AUS-adm2-2024-01_3hrly.tsv', sep='\t')
feb_data = init.pd.read_csv('ipobs-AUS-adm2-2024-02_3hrly.tsv', sep='\t')
mar_data = init.pd.read_csv('ipobs-AUS-adm2-2024-03_3hrly.tsv', sep='\t')
apr_data = init.pd.read_csv('ipobs-AUS-adm2-2024-04_3hrly.tsv', sep='\t')
may_data = init.pd.read_csv('ipobs-AUS-adm2-2024-05_3hrly.tsv', sep='\t')
jun_data = init.pd.read_csv('ipobs-AUS-adm2-2024-06_3hrly.tsv', sep='\t')
jul_data = init.pd.read_csv('ipobs-AUS-adm2-2024-07_3hrly.tsv', sep='\t')

print(jan_data.columns)

Index(['time_e', 'time_e_str', 'record_date', 'country_iso_three_char_code',
       'country_iso_name', 'adm1_name', 'adm2_name', 'adm1_unique_identifier',
       'adm2_unique_identifier', 'number_unique_active_ips_in_sample',
       'rtt_variance_norm', 'rtt_mean_norm', 'rtt_pctle_5', 'rtt_pctle_10',
       'rtt_pctle_25', 'rtt_pctle_50', 'rtt_pctle_75', 'rtt_pctle_90',
       'rtt_pctle_95', 'day_indicator'],
      dtype='object')


In [4]:
print('January data:', len(jan_data))
print('February data:', len(feb_data))
print('March data:', len(mar_data))
print('April data:', len(apr_data))
print('May data:', len(may_data))
print('June data:', len(jun_data))
print('July data:', len(jul_data))
print()
print('In total, there are', len(jan_data) + len(feb_data) + len(mar_data) + len(apr_data) + len(may_data) + len(jun_data) + len(jul_data), 'data points')

January data: 151214
February data: 141057
March data: 155269
April data: 153423
May data: 157985
June data: 151158
July data: 155911

In total, there are 1066017 data points


In [5]:
# FIRST RUN THROUGH WITH NO TIME CONSTRAINTS

def get_monthly(adm, state, data, hour = []):
    state_check = data[data['adm1_name'] == state]
    adm_check = state_check[state_check['adm2_name'] == adm]

    # Save us some time if it's empty anyway
    if len(adm_check) == 0:
        return [init.np.nan] * 8
    
    # Check the time for a specific time
    if hour != []:
        adm_check['datetime'] = init.pd.to_datetime(adm_check['time_e_str'])
        adm_check['datetime'] = adm_check['datetime'].dt.hour.astype(int)

        # Set the hour to 24 for all rows where the hour is 0
        adm_check.loc[adm_check['datetime'] == 0, 'datetime'] += 24
        adm_under = adm_check[adm_check['datetime'] >= hour[0]]
        adm_data = adm_under[adm_under['datetime'] <= hour[1]]

    else:
        adm_data = adm_check

    clean_5  = adm_data['rtt_pctle_5'].dropna()
    clean_10 = adm_data['rtt_pctle_10'].dropna()
    clean_25 = adm_data['rtt_pctle_25'].dropna()
    clean_50 = adm_data['rtt_pctle_50'].dropna()
    clean_75 = adm_data['rtt_pctle_75'].dropna()
    clean_90 = adm_data['rtt_pctle_90'].dropna()
    clean_95 = adm_data['rtt_pctle_95'].dropna()
    adm_5th = clean_5.mean()
    adm_10th = clean_10.mean()
    adm_25th = clean_25.mean()
    adm_50th = clean_50.mean()
    adm_75th = clean_75.mean()
    adm_90th = clean_90.mean()
    adm_95th = clean_95.mean()
    adm_sample = adm_data['number_unique_active_ips_in_sample'].mean()
    return [adm_5th, adm_10th, adm_25th, adm_50th, adm_75th, adm_90th, adm_95th, adm_sample]

adm2_json['5th Percentile']  = None
adm2_json['10th Percentile'] = None
adm2_json['25th Percentile'] = None
adm2_json['50th Percentile'] = None
adm2_json['75th Percentile'] = None
adm2_json['90th Percentile'] = None
adm2_json['95th Percentile'] = None
adm2_json['95th:5th Ratio']  = None
adm2_json['Sample Size']     = None

for ID in init.tqdm(adm2_json['fid']):
    adm = adm2_json[adm2_json['fid'] == ID]['name_2'].values[0]
    state = adm2_json[adm2_json['fid'] == ID]['name_1'].values[0]
    jan = get_monthly(adm, state, jan_data)
    feb = get_monthly(adm, state, feb_data)
    mar = get_monthly(adm, state, mar_data)
    apr = get_monthly(adm, state, apr_data)
    may = get_monthly(adm, state, may_data)
    jun = get_monthly(adm, state, jun_data)
    jul = get_monthly(adm, state, jul_data)
    
    months  = [jan, feb, mar, apr, may, jun, jul]
    perc_5  = [x[0] for x in months if not init.math.isnan(x[0])]
    perc_10 = [x[1] for x in months if not init.math.isnan(x[1])]
    perc_25 = [x[2] for x in months if not init.math.isnan(x[2])]
    perc_50 = [x[3] for x in months if not init.math.isnan(x[3])]
    perc_75 = [x[4] for x in months if not init.math.isnan(x[4])]
    perc_90 = [x[5] for x in months if not init.math.isnan(x[5])]
    perc_95 = [x[6] for x in months if not init.math.isnan(x[6])]
    sample  = [x[7] for x in months if not init.math.isnan(x[7])]

    if len(perc_5) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), '5th Percentile'] = sum(perc_5) / len(perc_5)

    if len(perc_10) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), '10th Percentile'] = sum(perc_10) / len(perc_10)

    if len(perc_25) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), '25th Percentile'] = sum(perc_25) / len(perc_25)

    if len(perc_50) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), '50th Percentile'] = sum(perc_50) / len(perc_50)

    if len(perc_75) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), '75th Percentile'] = sum(perc_75) / len(perc_75)

    if len(perc_90) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), '90th Percentile'] = sum(perc_90) / len(perc_90)

    if len(perc_95) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), '95th Percentile'] = sum(perc_95) / len(perc_95)

    if len(sample) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), 'Sample Size'] = sum(sample) / len(sample)

adm2_json['95th:5th Ratio'] = adm2_json['95th Percentile'] / adm2_json['5th Percentile']

100%|██████████| 1386/1386 [04:13<00:00,  5.46it/s]


In [6]:
print(adm2_json['Sample Size'][:10])

0    563.035639
1    150.990385
2          None
3          None
4          None
5      9.344599
6          None
7     62.321871
8          None
9     38.231475
Name: Sample Size, dtype: object


In [7]:
# SECOND RUN THROUGH WITH TIME RESTRAINTS

adm2_json['Busy 5th Percentile']  = None
adm2_json['Busy 10th Percentile'] = None
adm2_json['Busy 25th Percentile'] = None
adm2_json['Busy 50th Percentile'] = None
adm2_json['Busy 75th Percentile'] = None
adm2_json['Busy 90th Percentile'] = None
adm2_json['Busy 95th Percentile'] = None
adm2_json['Busy 95th:5th Ratio']  = None
adm2_json['Busy Sample Size']     = None

for ID in init.tqdm(adm2_json['fid']):
    adm = adm2_json[adm2_json['fid'] == ID]['name_2'].values[0]
    state = adm2_json[adm2_json['fid'] == ID]['name_1'].values[0]
    jan = get_monthly(adm, state, jan_data, [18,23])
    feb = get_monthly(adm, state, feb_data, [18,23])
    mar = get_monthly(adm, state, mar_data, [18,23])
    apr = get_monthly(adm, state, apr_data, [18,23])
    may = get_monthly(adm, state, may_data, [18,23])
    jun = get_monthly(adm, state, jun_data, [18,23])
    jul = get_monthly(adm, state, jul_data, [18,23])
    
    months  = [jan, feb, mar, apr, may, jun, jul]
    perc_5  = [x[0] for x in months if not init.math.isnan(x[0])]
    perc_10 = [x[1] for x in months if not init.math.isnan(x[1])]
    perc_25 = [x[2] for x in months if not init.math.isnan(x[2])]
    perc_50 = [x[3] for x in months if not init.math.isnan(x[3])]
    perc_75 = [x[4] for x in months if not init.math.isnan(x[4])]
    perc_90 = [x[5] for x in months if not init.math.isnan(x[5])]
    perc_95 = [x[6] for x in months if not init.math.isnan(x[6])]
    sample  = [x[7] for x in months if not init.math.isnan(x[7])]

    if len(perc_5) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), 'Busy 5th Percentile'] = sum(perc_5) / len(perc_5)

    if len(perc_10) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), 'Busy 10th Percentile'] = sum(perc_10) / len(perc_10)

    if len(perc_25) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), 'Busy 25th Percentile'] = sum(perc_25) / len(perc_25)

    if len(perc_50) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), 'Busy 50th Percentile'] = sum(perc_50) / len(perc_50)

    if len(perc_75) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), 'Busy 75th Percentile'] = sum(perc_75) / len(perc_75)

    if len(perc_90) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), 'Busy 90th Percentile'] = sum(perc_90) / len(perc_90)

    if len(perc_95) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), 'Busy 95th Percentile'] = sum(perc_95) / len(perc_95)

    if len(sample) != 0:
        adm2_json.loc[(adm2_json['name_2'] == adm) & (adm2_json['name_1'] == state), 'Busy Sample Size'] = sum(sample) / len(sample)

adm2_json['Busy 95th:5th Ratio'] = adm2_json['Busy 95th Percentile'] / adm2_json['Busy 5th Percentile']

  0%|          | 0/1386 [00:00<?, ?it/s]

C:\Users\43472\AppData\Local\Temp\ipykernel_2996\2520039614.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  adm_check['datetime'] = init.pd.to_datetime(adm_check['time_e_str'])
C:\Users\43472\AppData\Local\Temp\ipykernel_2996\2520039614.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  adm_check['datetime'] = adm_check['datetime'].dt.hour.astype(int)
C:\Users\43472\AppData\Local\Temp\ipykernel_2996\2520039614.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Dat

In [8]:
adm2_json['5th Percentile Change']  = adm2_json['Busy 5th Percentile']  - adm2_json['5th Percentile']
adm2_json['10th Percentile Change'] = adm2_json['Busy 10th Percentile'] - adm2_json['10th Percentile']
adm2_json['25th Percentile Change'] = adm2_json['Busy 25th Percentile'] - adm2_json['25th Percentile']
adm2_json['50th Percentile Change'] = adm2_json['Busy 50th Percentile'] - adm2_json['50th Percentile']
adm2_json['75th Percentile Change'] = adm2_json['Busy 75th Percentile'] - adm2_json['75th Percentile']
adm2_json['90th Percentile Change'] = adm2_json['Busy 90th Percentile'] - adm2_json['90th Percentile']
adm2_json['95th Percentile Change'] = adm2_json['Busy 95th Percentile'] - adm2_json['95th Percentile']
adm2_json['95th:5th Ratio Change']  = adm2_json['Busy 95th:5th Ratio']  - adm2_json['95th:5th Ratio']

In [9]:
adm2_json.to_file('corrected_australia_adm2_percentiles.json', driver='GeoJSON')

In [10]:
lgas = init.gpd.read_file('RA_australian_lgas.geojson')
lgas['RA fid'] = lgas['RA fid'] - 1
print(lgas.columns)

Index(['year', 'ste_code', 'ste_name', 'lga_code', 'lga_name', 'lga_area_code',
       'lga_type', 'lga_name_long', 'RA fid', 'geometry'],
      dtype='object')


In [11]:
# Just need a cell here to take the lga_codes from the new geojson and give it to the australian_lgas geojson
conversion = init.gpd.read_file('ADM_to_LGA_Conversion.geojson')
print(conversion.columns)

Index(['fid', 'gid', 'id_0', 'iso', 'name_0', 'id_1', 'name_1', 'id_2',
       'name_2', 'year', 'ste_code', 'ste_name', 'lga_code', 'lga_name',
       'lga_area_code', 'lga_type', 'lga_name_long', 'geometry'],
      dtype='object')


In [12]:
adm2_json['lga_code'] = conversion['lga_code']
print(adm2_json['lga_code'][:])

0       89399
1       89399
2       89399
3       89399
4       89399
        ...  
1381    59330
1382    59340
1383    59350
1384    59360
1385    59370
Name: lga_code, Length: 1386, dtype: object


In [13]:
lgas['5th Percentile']  = None
lgas['10th Percentile'] = None
lgas['25th Percentile'] = None
lgas['50th Percentile'] = None
lgas['75th Percentile'] = None
lgas['90th Percentile'] = None
lgas['95th Percentile'] = None
lgas['95th:5th Ratio']  = None
lgas['Sample Size']     = None
lgas['centroids']       = lgas['geometry'].centroid
lgas['Busy 5th Percentile']  = None
lgas['Busy 10th Percentile'] = None
lgas['Busy 25th Percentile'] = None
lgas['Busy 50th Percentile'] = None
lgas['Busy 75th Percentile'] = None
lgas['Busy 90th Percentile'] = None
lgas['Busy 95th Percentile'] = None
lgas['Busy 95th:5th Ratio']  = None
lgas['Busy Sample Size']     = None
lgas['5th Percentile Change']  = None
lgas['10th Percentile Change'] = None
lgas['25th Percentile Change'] = None
lgas['50th Percentile Change'] = None
lgas['75th Percentile Change'] = None
lgas['90th Percentile Change'] = None
lgas['95th Percentile Change'] = None
lgas['95th:5th Ratio Change']  = None

def new_average(measurements, samples):
    # Remove cases with no measurements
    if len(measurements) == 0:
        return None
    
    # Otherwise, calculate the weighted average
    else:
        measurement_sum = 0
        for idx in range(len(measurements)):
            measurement_sum += measurements[idx] * samples[idx]

    return measurement_sum / sum(samples)

missing_lgas = init.gpd.GeoDataFrame()

for lga in init.tqdm(lgas['lga_code']):
    adm2_json_lgas = adm2_json[adm2_json['lga_code'] == lga]
    if len(adm2_json_lgas) == 0:
        temp_df = lgas[lgas['lga_code'] == lga]
        missing_lgas = init.pd.concat([missing_lgas, temp_df], ignore_index=True)

    else:
        # Calculate the regulars
        lgas.loc[lgas['lga_code'] == lga, '5th Percentile'] = new_average([x for x in list(adm2_json_lgas['5th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Sample Size']) if x is not None])
        lgas.loc[lgas['lga_code'] == lga, '10th Percentile'] = new_average([x for x in list(adm2_json_lgas['10th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Sample Size']) if x is not None])
        lgas.loc[lgas['lga_code'] == lga, '25th Percentile'] = new_average([x for x in list(adm2_json_lgas['25th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Sample Size']) if x is not None])
        lgas.loc[lgas['lga_code'] == lga, '50th Percentile'] = new_average([x for x in list(adm2_json_lgas['50th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Sample Size']) if x is not None])
        lgas.loc[lgas['lga_code'] == lga, '75th Percentile'] = new_average([x for x in list(adm2_json_lgas['75th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Sample Size']) if x is not None])
        lgas.loc[lgas['lga_code'] == lga, '90th Percentile'] = new_average([x for x in list(adm2_json_lgas['90th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Sample Size']) if x is not None])
        lgas.loc[lgas['lga_code'] == lga, '95th Percentile'] = new_average([x for x in list(adm2_json_lgas['95th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Sample Size']) if x is not None])

        # Calculate the busys
        lgas.loc[lgas['lga_code'] == lga, 'Busy 5th Percentile'] = new_average([x for x in list(adm2_json_lgas['Busy 5th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Busy Sample Size']) if x is not None])
        lgas.loc[lgas['lga_code'] == lga, 'Busy 10th Percentile'] = new_average([x for x in list(adm2_json_lgas['Busy 10th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Busy Sample Size']) if x is not None])
        lgas.loc[lgas['lga_code'] == lga, 'Busy 25th Percentile'] = new_average([x for x in list(adm2_json_lgas['Busy 25th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Busy Sample Size']) if x is not None])
        lgas.loc[lgas['lga_code'] == lga, 'Busy 50th Percentile'] = new_average([x for x in list(adm2_json_lgas['Busy 50th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Busy Sample Size']) if x is not None])
        lgas.loc[lgas['lga_code'] == lga, 'Busy 75th Percentile'] = new_average([x for x in list(adm2_json_lgas['Busy 75th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Busy Sample Size']) if x is not None])
        lgas.loc[lgas['lga_code'] == lga, 'Busy 90th Percentile'] = new_average([x for x in list(adm2_json_lgas['Busy 90th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Busy Sample Size']) if x is not None])
        lgas.loc[lgas['lga_code'] == lga, 'Busy 95th Percentile'] = new_average([x for x in list(adm2_json_lgas['Busy 95th Percentile']) if x is not None], [x for x in list(adm2_json_lgas['Busy Sample Size']) if x is not None])

        # Calculate the ratios
        lgas.loc[lgas['lga_code'] == lga, '95th:5th Ratio']  = lgas.loc[lgas['lga_code'] == lga, '95th Percentile'] / lgas.loc[lgas['lga_code'] == lga, '5th Percentile']
        lgas.loc[lgas['lga_code'] == lga, 'Busy 95th:5th Ratio']  = lgas.loc[lgas['lga_code'] == lga, 'Busy 95th Percentile'] / lgas.loc[lgas['lga_code'] == lga, 'Busy 5th Percentile']

        # Calculate the changes
        lgas.loc[lgas['lga_code'] == lga, '5th Percentile Change']  = lgas.loc[lgas['lga_code'] == lga, 'Busy 5th Percentile']  - lgas.loc[lgas['lga_code'] == lga, '5th Percentile']
        lgas.loc[lgas['lga_code'] == lga, '10th Percentile Change'] = lgas.loc[lgas['lga_code'] == lga, 'Busy 10th Percentile'] - lgas.loc[lgas['lga_code'] == lga, '10th Percentile']
        lgas.loc[lgas['lga_code'] == lga, '25th Percentile Change'] = lgas.loc[lgas['lga_code'] == lga, 'Busy 25th Percentile'] - lgas.loc[lgas['lga_code'] == lga, '25th Percentile']
        lgas.loc[lgas['lga_code'] == lga, '50th Percentile Change'] = lgas.loc[lgas['lga_code'] == lga, 'Busy 50th Percentile'] - lgas.loc[lgas['lga_code'] == lga, '50th Percentile']
        lgas.loc[lgas['lga_code'] == lga, '75th Percentile Change'] = lgas.loc[lgas['lga_code'] == lga, 'Busy 75th Percentile'] - lgas.loc[lgas['lga_code'] == lga, '75th Percentile']
        lgas.loc[lgas['lga_code'] == lga, '90th Percentile Change'] = lgas.loc[lgas['lga_code'] == lga, 'Busy 90th Percentile'] - lgas.loc[lgas['lga_code'] == lga, '90th Percentile']
        lgas.loc[lgas['lga_code'] == lga, '95th Percentile Change'] = lgas.loc[lgas['lga_code'] == lga, 'Busy 95th Percentile'] - lgas.loc[lgas['lga_code'] == lga, '95th Percentile']
        lgas.loc[lgas['lga_code'] == lga, '95th:5th Ratio Change']  = lgas.loc[lgas['lga_code'] == lga, 'Busy 95th:5th Ratio']  - lgas.loc[lgas['lga_code'] == lga, '95th:5th Ratio']

print('There are', len(missing_lgas),' missing LGAs')

if len(missing_lgas) != 0:
    for i in range(len(missing_lgas)):
        print('Missing LGA #', i+1,'is:', missing_lgas['lga_name'].values[i], 'in', missing_lgas['ste_name'].values[i])

C:\Users\43472\AppData\Local\Temp\ipykernel_2996\1713560636.py:10: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  lgas['centroids']       = lgas['geometry'].centroid
100%|██████████| 547/547 [00:22<00:00, 24.56it/s]

There are 3  missing LGAs
Missing LGA # 1 is: Darwin Waterfront Precinct in Northern Territory
Missing LGA # 2 is: Christmas Island in Other Territories
Missing LGA # 3 is: Cocos Islands in Other Territories


In [14]:
lgas.drop('centroids', axis=1, inplace=True)
lgas.to_file('australian_lgas_with_rtt.geojson', driver='GeoJSON')

In [ ]:
adm2_json['centroids'] = adm2_json['geometry'].centroid

from shapely.geometry import Point

def find_containing_geometries(gdf, point):
    """
    Find geometries in the GeoDataFrame that contain the specified point.
    
    Parameters:
    gdf (GeoDataFrame): GeoDataFrame containing the geometries.
    point (shapely.geometry.Point): Point to check against the geometries.

    Returns:
    GeoDataFrame: GeoDataFrame with geometries that contain the point.
    """
    # Ensure the point is a Shapely Point object
    if not isinstance(point, Point):
        raise ValueError("The provided point is not a Shapely Point object.")
    
    # Check which geometries contain the point
    containing_geometries = gdf[gdf['geometry'].apply(lambda geom: geom.contains(point))]
    
    return containing_geometries

from shapely.ops import nearest_points

def snap_point_to_nearest_lga(regions, point, buffer_distance=0.001):
    # Create a small buffer around the point
    point_buffer = point.buffer(buffer_distance)

    # Check if the buffered point intersects with any LGA
    intersecting_lgas = lgas[lgas.intersects(point_buffer)]
    
    if not intersecting_lgas.empty:
        # If the buffered point intersects with one or more LGAs, find the closest LGA
        distances = intersecting_lgas.distance(point)
        nearest_lga_index = distances.idxmin()
        nearest_lga = intersecting_lgas.loc[nearest_lga_index]
        
        # Snap point to the nearest boundary of the nearest LGA
        snapped_point = nearest_points(point, nearest_lga.geometry.boundary)[1]
        
        # Ensure the snapped point is inside the nearest LGA
        if nearest_lga.geometry.contains(snapped_point):
            return snapped_point
        
        # If the snapped point is not within the nearest LGA, try to find a valid point
        else:
            # Use the `nearest_points` function to ensure the point is within the boundary
            snapped_point = nearest_lga.geometry.representative_point()
            return snapped_point
    
    # If no LGA intersects with the buffered point, find the nearest LGA and snap to its boundary
    distances = lgas.distance(point)
    nearest_lga_index = distances.idxmin()
    nearest_lga = lgas.loc[nearest_lga_index]
    
    # Snap point to the nearest boundary of the nearest LGA
    snapped_point = nearest_points(point, nearest_lga.geometry.boundary)[1]
    
    # Check if the snapped point is inside the LGA, and if not, adjust
    if nearest_lga.geometry.contains(snapped_point):
        return snapped_point
    else:
        # If not inside, use the LGA's representative point (a point guaranteed to be inside)
        return nearest_lga.geometry.representative_point()

# lga_plot should be 0-2 (range of 3)
lga_plot = 1
bounds = 0.05

# Plot the polygons
fig, ax = init.plt.subplots(figsize=(6, 6))  # Create figure and axis

# Plot the polygons on the axis
lgas.plot(ax=ax, edgecolor='black', facecolor='lightblue')

# Optional: Add titles or labels
ax.set_title('LGA OVERLAY, MISSING #' + str(lga_plot))
ax.set_xlabel('Longitude')
ax.set_ylabel('Latitude')

# Extract a single point from the 'centroids' column
point_geom = missing_lgas.iloc[lga_plot]['centroids']

# Plot the point on the same axis
ax.plot(point_geom.x, point_geom.y, 'o', color='red', label = 'missing lga centroid')  # 'o' for point marker
missing_lgas.plot(ax=ax, edgecolor='red',facecolor='lightblue')

# Set axis limits based on the point's coordinates
init.plt.xlim(point_geom.x - bounds, point_geom.x + bounds)
init.plt.ylim(point_geom.y - bounds, point_geom.y + bounds)

print('This is', missing_lgas.iloc[lga_plot]['lga_name_long'],'in', missing_lgas.iloc[lga_plot]['ste_name'])

# Show the plot
init.plt.gca().legend()
init.plt.show()

######## VISUALISE ADM2s ########

# Plot the polygons
fig, ax = init.plt.subplots(figsize=(6, 6))  # Create figure and axis

# Plot the polygons on the axis
adm2_json.plot(ax=ax, edgecolor='black', facecolor='lightblue')

# Optional: Add titles or labels
ax.set_title('ADM OVERLAY')
ax.set_xlabel('Longitude')
ax.set_ylabel('Latitude')

# Extract a single point from the 'centroids' column
point_geom = missing_lgas.iloc[lga_plot]['centroids']

# Plot the point on the same axis
ax.plot(point_geom.x, point_geom.y, 'o', color='red', label = 'missing lga centroid')  # 'o' for point marker

# Set axis limits based on the point's coordinates
init.plt.xlim(point_geom.x - bounds, point_geom.x + bounds)
init.plt.ylim(point_geom.y - bounds, point_geom.y + bounds)

# Call the function
chosen_adm2 = find_containing_geometries(adm2_json, point_geom)
# In case point_geom is not mainland Australia
if chosen_adm2.empty:
    snap_point = snap_point_to_nearest_lga(adm2_json, point_geom)
    chosen_adm2 = find_containing_geometries(adm2_json, snap_point)
chosen_adm2_name = chosen_adm2['name_2']
print('Corresponding ADM2 is', chosen_adm2_name)

allocated_lga_code = chosen_adm2.iloc[0]['lga_code']
allocated_lga_name = lgas[lgas['lga_code'] == allocated_lga_code]['lga_name']
print('But', chosen_adm2_name,' was allocated to', lgas[lgas['lga_code'] == allocated_lga_code]['lga_name'].to_string())
chosen = lgas[lgas['lga_code'] == allocated_lga_code]

# Plot the polygons on the axis
chosen.plot(ax=ax, edgecolor='red')
centroid = chosen['centroids']
ax.plot(centroid.x, centroid.y, 'o', color='black', label='adm centroid')

init.plt.gca().legend()
init.plt.show()

######## VISUALISE LGAs ########

# Plot the polygons
fig, ax = init.plt.subplots(figsize=(6, 6))  # Create figure and axis

# Plot the polygons on the axis
lgas.plot(ax=ax, edgecolor='black', facecolor='lightblue')

# Optional: Add titles or labels
ax.set_title('ALLOCATED LGA, #' + str(lga_plot))
ax.set_xlabel('Longitude')
ax.set_ylabel('Latitude')

# Extract a single point from the 'centroids' column
#point_geom = chosen['centroids']
allocated_lga = lgas[lgas['lga_code'] == chosen.iloc[0]['lga_code']]
allocated_lga.plot(ax=ax, edgecolor='red')

# Plot the point on the same axis
#ax.plot(point_geom.x, point_geom.y, 'o', color='red')  # 'o' for point marker
init.plt.plot(allocated_lga['centroids'].x, allocated_lga['centroids'].y, 'o', color='red', label = 'allocated lga centroid')

# Extract the single geometry from the GeoSeries
#point_geom = chosen['centroids'].iloc[0]  # Get the single geometry
point_geom = missing_lgas.iloc[lga_plot]['centroids']

# Set axis limits based on the point's coordinates
ax.set_xlim(point_geom.x - bounds, point_geom.x + bounds)
ax.set_ylim(point_geom.y - bounds, point_geom.y + bounds)

print('This is', allocated_lga['lga_name_long'].to_string(),', lga code', chosen.iloc[0]['lga_code'])

# Show the plot
init.plt.gca().legend()
init.plt.show()